# Programming Project - Unit 2
*by Débora Azevedo, Eliseu Jayro, Francisco de Paiva and Igor Brandão*

**Goals**
The purpose of this project is explore the following:

- Access Health Graph API - Runkeeper content;
- Geolocation analysis and hypotheses should be explained in detail;

<hr>

# Global Imports section

Import the necessary libraries to handle 

- Geocoding;
- Maps;
- File input;
- Heatmap;
- Numpy library;
- Tqdm progress bar

In [ ]:
### Library necessary to run this IPython Notebook
!pip install geocoder
!pip install folium
!pip install tqdm
!pip install tabulate
!pip install pandas-datareader

In [ ]:
# Import pandas
import pandas as pd

# Import google geocoder
import geocoder as gc

# Import numpy library
import numpy as np

# Import folium heatmap
import folium
from folium.plugins import HeatMap

# Import tqdm progressing bar plugin
from tqdm import tqdm

<hr>

# I - Maps section

## Geolocation data import [optional]

In [ ]:
# Import the fertility.csv data: data
geolocation_data = pd.read_csv("geolocation.csv", encoding = 'latin2')

### Coordinate groupping

The cell below perform the latitude/longitude reading and count all og them to know if there are repetitions and group *[latitude, longitude, count]* data into the coordinate array

In [ ]:
# =================================================================================
# Data adjusts
# =================================================================================

# Count the same latitude/longitude occurrences
geodata = geolocation_data.groupby(['longitude', 'latitude']).size().reset_index().rename(columns={0:'count'})

# =================================================================================
# Add the coordinates
# =================================================================================

# Initialize the coordinates array
coordinates = []

# Add the coordinates to the coordinate
for i in tqdm(range(len(geodata))):
    # eliminate items with'nan' element
    if all(~np.isnan([geodata.loc[geodata.index[i],'latitude'], geodata.loc[geodata.index[i],'longitude'], geodata.loc[geodata.index[i],'count']])):
        coordinates.append([geodata.loc[geodata.index[i],'latitude'], geodata.loc[geodata.index[i],'longitude'], geodata.loc[geodata.index[i],'count']])

# Display the imported coordinates
coordinates

## 1) Heatmap

In [14]:
# =================================================================================
# Heatmap generation
# =================================================================================

# Set map center and zoom level
mapc = [-5.788, -35.202]
zoom = 11

# Create map object
htMap = folium.Map(location=mapc, zoom_start=zoom)

# Append the coordinates to the heatMap
HeatMap(coordinates).add_to(htMap)

# Print the heatMap
htMap

### 1.1) Heatmap by activity

In [ ]:
# =================================================================================
# API single activity request
# =================================================================================

# Copy the data
single_geolocation_data = pd.DataFrame()

# Base URI
activity_id = 902920684

activity_base_URI = "http://api.runkeeper.com/fitnessActivities/"

# Final activity URI
single_activity_url = activity_base_URI + str(activity_id) + "?access_token=" + ACCESS_TOKEN

# Receive the results from API
single_activity_content = requests.get(single_activity_url).json()

# Perform a conversion from JSON to Data Frame
single_activity_df = json_normalize(single_activity_content['path'])

# Add the activity path data to geolocation
single_geolocation_data = pd.concat([single_geolocation_data, single_activity_df])

# =================================================================================
# Data adjusts
# =================================================================================

# Count the same latitude/longitude occurrences
single_geodata = single_geolocation_data.groupby(['longitude', 'latitude']).size().reset_index().rename(columns={0:'count'})

# =================================================================================
# Heatmap generation
# =================================================================================

# Set map center and zoom level
mapc = [-5.788, -35.202]
zoom = 11

# Initialize the coordinates array
coordinates = []

# Add the coordinates to the coordinate
for i in tqdm(range(len(single_geodata))):
    # eliminate items with'nan' element
    if all(~np.isnan([single_geodata.ix[i,'latitude'], single_geodata.ix[i,'longitude'], single_geodata.ix[i,'count']])):
        coordinates.append([single_geodata.ix[i,'latitude'], single_geodata.ix[i,'longitude'], single_geodata.ix[i,'count']])

# Create map object
htMap = folium.Map(location=mapc, zoom_start=zoom)

# Append the coordinates to the heatMap
HeatMap(coordinates).add_to(htMap)

# ==========================================================
# Display activites summary
# ==========================================================
display(Markdown('## Activity summary'))

display(Markdown('** Activity type:** ' + str(single_activity_content['type'])))

display(Markdown('** Datetime:** ' + str(single_activity_content['start_time'])))

distance = (single_activity_content['total_distance'])/1000
display(Markdown('** Total distance:** ' + str("%.2f" % distance) + ' km'))

climb = (single_activity_content['climb'])
display(Markdown('** Total climb:** ' + str("%.2f" % climb) + ' mts'))

htMap

## 2) Map markers

In [ ]:
# =================================================================================
# Data adjusts
# =================================================================================

# Count the same latitude/longitude occurrences
geodata = geolocation_data.groupby(['longitude', 'latitude']).size().reset_index().rename(columns={0:'count'})

# =================================================================================
# Map markers generation
# =================================================================================

# Set map center and zoom level
mapc = [-5.788, -35.202]
zoom = 11

# For speed purposes
MAX_RECORDS = 2000

# Create map object
map_activities = folium.Map(location=mapc, zoom_start=zoom)

marker_cluster = folium.MarkerCluster("Activities").add_to(map_activities)

# Add the coordinates to the coordinate
for i in tqdm(range(len(geodata))):
    
    if i == MAX_RECORDS:
        break;
    
    # eliminate items with'nan' element
    if all(~np.isnan([geodata.ix[i,'latitude'], geodata.ix[i,'longitude']])):
        folium.Marker(location = [geodata.ix[i,'latitude'],geodata.ix[i,'longitude']]).add_to(marker_cluster)

# Show the map
map_activities